# FastAI Tabular Starter Notebook by @johnowhitaker
<table style="margin: 0px auto;"><tr>
<td> 
<img src="https://gitlab.aicrowd.com/aicrowd/assets/-/raw/master/challenges/clock-decomposition/notebook-banner.jpg?inline=false" alt="Drawing" width='250px'/> 
</td>
</tr></table>


# What is the notebook about?

The challenge is to use the features extracted from the Clock Drawing Test to build an automated and algorithm to predict whether each participant is one of three phases:

1)    Pre-Alzheimer’s (Early Warning)
2)    Post-Alzheimer’s (Detection)
3)    Normal (Not an Alzheimer’s patient)

In this starter notebook we will solve this task using fastai. Make sure you don't edit out the section headings as AICROWD uses these to split this notebook up for submission. All code that is needed for both train and test goes in the preprocessing section, for example. I've tried to highlight where I've added code that isn't in the original template.

- **Installing packages**. Please use the [Install packages 🗃](#install-packages-) section to install the packages
- **Training your models**. All the code within the [Training phase ⚙️](#training-phase-) section will be skipped during evaluation. **Please make sure to save your model weights in the assets directory and load them in the predictions phase section** 

# Setup AIcrowd Utilities 🛠

We use this to bundle the files for submission and create a submission on AIcrowd. Do not edit this block.

In [1]:
!pip install -q -U aicrowd-cli

In [2]:
%load_ext aicrowd.magic

# AIcrowd Runtime Configuration 🧷

Define configuration parameters. Please include any files needed for the notebook to run under `ASSETS_DIR`. We will copy the contents of this directory to your final submission file 🙂

The dataset is available under `/ds_shared_drive` on the workspace.

In [3]:
import os

# Please use the absolute for the location of the dataset.
# Or you can use relative path with `os.getcwd() + "test_data/validation.csv"`
AICROWD_DATASET_PATH = os.getenv("DATASET_PATH", "/ds_shared_drive/validation.csv")
AICROWD_PREDICTIONS_PATH = os.getenv("PREDICTIONS_PATH", "predictions.csv")
AICROWD_ASSETS_DIR = "assets"
AICROWD_API_KEY = "" # Get your key from https://www.aicrowd.com/participants/me

# Install packages 🗃

Please add all pacakage installations in this section

In [4]:
!pip install -q numpy pandas scikit-learn
!pip install -q -U fastcore fastai # Need -U otherwise we're stuck with an old version on their docker

# Define preprocessing code 💻

The code that is common between the training and the prediction sections should be defined here. During evaluation, we completely skip the training section. Please make sure to add any common logic between the training and prediction sections here.

### Import common packages

Please import packages that are common for training and prediction phases here.

In [5]:
import numpy as np
import pandas as pd
from sklearn.metrics import f1_score, log_loss
from fastai.tabular.all import *

# Training phase ⚙️

You can define your training code here. This sections will be skipped during evaluation.

In [6]:
# Loading the training data
df = pd.read_csv(os.getenv("DATASET_PATH", "/ds_shared_drive/train.csv"))
print(df.shape)
df.head()

(32777, 122)


row_id  number_of_digits  missing_digit_1  missing_digit_2  \
0  S0CIXBKIUEOUBNURP              12.0              0.0              0.0   
1  IW1Z4Z3H720OPW8LL              12.0              0.0              0.0   
2  PVUGU14JRSU44ZADT              12.0              0.0              0.0   
3  RW5UTGMB9H67LWJHX               7.0              0.0              0.0   
4  W0IM2V6F6UP5LYS3E              12.0              0.0              0.0   

   missing_digit_3  missing_digit_4  missing_digit_5  missing_digit_6  \
0              0.0              0.0              0.0              0.0   
1              0.0              0.0              0.0              0.0   
2              0.0              0.0              0.0              0.0   
3              0.0              1.0              0.0              0.0   
4              0.0              0.0              0.0              0.0   

   missing_digit_7  missing_digit_8  ...  bottom_area_perc  left_area_perc  \
0              0.0              0.0  ...          0.526170        0.524975   
1              0.0              0.0  ...          0.000810        0.516212   
2              0.0              0.0  ...          0.488109        0.550606   
3              1.0              1.0  ...               NaN             NaN   
4              0.0              0.0  ...          0.512818        0.511865   

   right_area_perc  hor_count  vert_count  eleven_ten_error  other_error  \
0         0.474667          0           0                 0            1   
1         0.483330          0           1                 0            1   
2         0.449042          0           0                 0            0   
3              NaN          1           0                 0            1   
4         0.487791          0           1                 0            0   

   time_diff  centre_dot_detect  diagnosis  
0     -105.0                0.0     normal  
1        NaN                NaN     normal  
2        0.0                0.0     normal  
3        NaN                NaN     normal  
4        0.0                1.0     normal  

[5 rows x 122 columns]

Following the example in the fastai docs, we construct our dataloaders:

In [7]:
splits = RandomSplitter(valid_pct=0.2)(range_of(df))
to = TabularPandas(df.fillna(0), procs=[Categorify, FillMissing,Normalize],
                   cat_names = ['intersection_pos_rel_centre'],
                   cont_names = list(df.drop(['row_id', 'intersection_pos_rel_centre', 'diagnosis'], axis=1).columns),
                   y_names='diagnosis',
                   splits=splits)
dls = to.dataloaders(bs=64)
dls.show_batch()

With these done, we can create a learner and train it for a short while. 

In [8]:
learn = tabular_learner(dls, metrics=accuracy)
learn.fit_one_cycle(5)

We're getting a log loss of 0.17 on our validation set, which is a random sub-sample of train. However, we should really look at the score on the provided validation set, which more closely matches the test set:

In [9]:
val = pd.read_csv(os.getenv("DATASET_PATH", "/ds_shared_drive/validation.csv"))
val = pd.merge(val, pd.read_csv(os.getenv("DATASET_PATH", "/ds_shared_drive/validation_ground_truth.csv")), 
               how='left', on='row_id')
print(val.shape)
test_dl = learn.dls.test_dl(val.fillna(0))
probs, y = learn.get_preds(dl=test_dl)
print('Log Loss on provided validation set:', log_loss(val['diagnosis'].values, probs.numpy()))

(362, 122)


Log Loss on provided validation set: 0.7788187272655996


Saving the trained model is as easy as:

In [10]:
learn.export(AICROWD_ASSETS_DIR + '/fai_model1.mdl')

# Prediction phase 🔎

Please make sure to save the weights from the training section in your assets directory and load them in this section

In [11]:
learn = load_learner(AICROWD_ASSETS_DIR + '/fai_model1.mdl') # load the model

## Load test data

In [12]:
test_data = pd.read_csv(AICROWD_DATASET_PATH)
test_data.head()

row_id  number_of_digits  missing_digit_1  missing_digit_2  \
0  LA9JQ1JZMJ9D2MBZV              11.0              0.0              0.0   
1  PSSRCWAPTAG72A1NT               6.0              1.0              1.0   
2  GCTODIZJB42VCBZRZ              11.0              0.0              0.0   
3  7YMVQGV1CDB1WZFNE               3.0              1.0              0.0   
4  PHEQC6DV3LTFJYIJU               1.0              1.0              1.0   

   missing_digit_3  missing_digit_4  missing_digit_5  missing_digit_6  \
0              0.0              0.0              0.0              0.0   
1              0.0              1.0              1.0              0.0   
2              0.0              0.0              1.0              0.0   
3              1.0              0.0              1.0              1.0   
4              1.0              1.0              1.0              1.0   

   missing_digit_7  missing_digit_8  ...  top_area_perc  bottom_area_perc  \
0              0.0              0.0  ...       0.500272          0.499368   
1              0.0              0.0  ...       0.572472          0.427196   
2              0.0              0.0  ...       0.494076          0.505583   
3              1.0              1.0  ...       0.555033          0.444633   
4              1.0              0.0  ...       0.603666          0.395976   

   left_area_perc  right_area_perc  hor_count  vert_count  eleven_ten_error  \
0        0.553194         0.446447          0           0                 0   
1        0.496352         0.503273          0           1                 0   
2        0.503047         0.496615          1           0                 0   
3        0.580023         0.419575          0           1                 0   
4        0.494990         0.504604          0           0                 0   

   other_error  time_diff  centre_dot_detect  
0            1        NaN                NaN  
1            1        NaN                NaN  
2            0        0.0                0.0  
3            1        NaN                NaN  
4            1      150.0                0.0  

[5 rows x 121 columns]

## Generate predictions

In [13]:
test_dl = learn.dls.test_dl(test_data.fillna(0)) # New dataloader with the test data
preds, _ = learn.get_preds(dl=test_dl)
preds = preds.numpy() # Convert to numpy array 
predictions = {
    "row_id": test_data["row_id"].values,
    "normal_diagnosis_probability": [p[0] for p in preds],
    "post_alzheimer_diagnosis_probability":  [p[1] for p in preds],
    "pre_alzheimer_diagnosis_probability":  [p[2] for p in preds],
}

predictions_df = pd.DataFrame.from_dict(predictions)
predictions_df.head(3)

row_id  normal_diagnosis_probability  \
0  LA9JQ1JZMJ9D2MBZV                      0.958330   
1  PSSRCWAPTAG72A1NT                      0.841258   
2  GCTODIZJB42VCBZRZ                      0.998962   

   post_alzheimer_diagnosis_probability  pre_alzheimer_diagnosis_probability  
0                              0.024677                             0.016993  
1                              0.080386                             0.078356  
2                              0.000609                             0.000428

## Save predictions 📨

In [14]:
predictions_df.to_csv(AICROWD_PREDICTIONS_PATH, index=False)

# Submit to AIcrowd 🚀

**NOTE: PLEASE SAVE THE NOTEBOOK BEFORE SUBMITTING IT (Ctrl + S)**

In [15]:
!aicrowd login --api-key $AICROWD_API_KEY
!DATASET_PATH=$AICROWD_DATASET_PATH \
aicrowd notebook submit \
    --assets-dir $AICROWD_ASSETS_DIR \
    --challenge addi-alzheimers-detection-challenge

API Key valid
Saved API Key successfully!
Using notebook: /home/desktop0/FastAI Tabular Starter Notebook.ipynb for submission...
Removing existing files from submission directory...
Scrubbing API keys from the notebook...
Validating the submission...
Executing install.ipynb...
[NbConvertApp] Converting notebook /home/desktop0/submission/install.ipynb to notebook
[NbConvertApp] Executing notebook with kernel: python
[NbConvertApp] Writing 1325 bytes to /home/desktop0/submission/install.nbconvert.ipynb
Executing predict.ipynb...
[NbConvertApp] Converting notebook /home/desktop0/submission/predict.ipynb to notebook
[NbConvertApp] Executing notebook with kernel: python
[NbConvertApp] Writing 19616 bytes to /home/desktop0/submission/predict.nbconvert.ipynb
submission.zip ━━━━━━━━━━━━━━━━━━━━━━ 100.0% • 1.4/1.4 MB • 856.0 kB/s • 0:00:00 • 0:00:010:00:01
                                                 ╭─────────────────────────╮                                                 
              